In [1]:
import pandas as pd
import numpy as np
from pandas import Series, DataFrame
from tqdm import tqdm

users = pd.read_csv('../../../dataset/userid-profile.tsv', sep='\t', header=0, index_col='#id')

listening_history = pd.read_csv('../../../dataset/userid-timestamp-artid-artname-traid-traname.tsv', sep='\t', encoding='utf8', header=None, error_bad_lines=False)
listening_history.columns = ["#id", "timestamp ", "artist-id", "artist-name", "track-id","track-name"]

b'Skipping line 2120260: expected 6 fields, saw 8\n'
b'Skipping line 2446318: expected 6 fields, saw 8\n'
b'Skipping line 11141081: expected 6 fields, saw 8\n'
b'Skipping line 11152099: expected 6 fields, saw 12\nSkipping line 11152402: expected 6 fields, saw 8\n'
b'Skipping line 11882087: expected 6 fields, saw 8\n'
b'Skipping line 12902539: expected 6 fields, saw 8\nSkipping line 12935044: expected 6 fields, saw 8\n'
b'Skipping line 17589539: expected 6 fields, saw 8\n'


In [2]:
# get_user_id
users_us = users[users['country']=='United States'].reset_index()

In [3]:
# reset index
listening_history_us = listening_history.set_index('#id').loc[users_us['#id']]
listening_history_us = listening_history_us.reset_index()

In [4]:
#calculate  the distirbution of the users
unique_users = listening_history_us['#id'].unique()
unique_tracks = listening_history_us['track-name'].unique()
print ('Number of unique users : ' + str(len(unique_users)))
print ('Number of unique tracks : ' + str(len(unique_tracks)))
print ('Times of tracks being listened: ' + str(len(listening_history_us)))

Number of unique users : 228
Number of unique tracks : 448129
Times of tracks being listened: 5016564


In [6]:
# remap the users
track_keys = {}

for track in unique_tracks:
    track_keys[track] = len(track_keys)
    
user_keys = {}

for user in unique_users:
    user_keys[user] = len(user_keys)
    
unique_user = len(unique_users)
unique_track = len(unique_tracks)
    

In [7]:
listening_history_us['tid']= listening_history_us['track-name'].map(track_keys)
listening_history_us['uid']= listening_history_us['#id'].map(user_keys)

In [8]:
lh = listening_history_us[['uid','tid']]

In [9]:
lh['count'] = 1

/home/han/anaconda3/envs/ts/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


In [10]:
lh = lh.groupby(["uid", "tid"]).sum().reset_index()
lh

uid     tid  count
0          0       0      1
1          0       1      1
2          0       2      1
3          0       3      1
4          0       4     15
5          0       5      3
6          0       6      1
7          0       7      1
8          0       8     10
9          0       9      1
10         0      10      2
11         0      11      3
12         0      12      3
13         0      13      2
14         0      14      1
15         0      15      2
16         0      16      1
17         0      17      2
18         0      18      1
19         0      19      1
20         0      20      1
21         0      21      2
22         0      22      1
23         0      23      1
24         0      24      1
25         0      25      3
26         0      26      2
27         0      27      3
28         0      28      1
29         0      29      1
...      ...     ...    ...
1257822  227  448099      1
1257823  227  448100      1
1257824  227  448101      1
1257825  227  448102      1
1257826  227  448103      1
1257827  227  448104      1
1257828  227  448105      1
1257829  227  448106      1
1257830  227  448107      1
1257831  227  448108      1
1257832  227  448109      1
1257833  227  448110      1
1257834  227  448111      1
1257835  227  448112      1
1257836  227  448113      1
1257837  227  448114      1
1257838  227  448115      1
1257839  227  448116      1
1257840  227  448117      1
1257841  227  448118      1
1257842  227  448119      1
1257843  227  448120      1
1257844  227  448121      1
1257845  227  448122      1
1257846  227  448123      1
1257847  227  448124      1
1257848  227  448125      1
1257849  227  448126      1
1257850  227  448127      1
1257851  227  448128      1

[1257852 rows x 3 columns]

In [11]:
lh.to_pickle('../data/counting.pkl')

In [12]:
max_list = []
for i in lh['uid'].unique():
    user = lh[lh['uid'] == i]
    max_value = max(user['count'])
    max_list.append(max_value)

In [12]:
counting_list = []
for i in range(0, unique_user):
    counting_list.append(np.zeros(unique_track, dtype=np.int))

In [13]:
for i in tqdm(range(unique_track)):
    temp = lh[lh['tid'] == i]
    for index, row in temp.iterrows():
        uindex = int(row['uid'])
        counting_list[uindex][i] = row['count']

100%|██████████| 448129/448129 [08:55<00:00, 837.09it/s]


In [14]:
np.savetxt("../data/counting_list.csv", counting_list, delimiter=",", fmt='%d')

In [ ]:
#minmax

In [15]:
normalized_list = []
for i in range(0, unique_user):
    normalized_list.append(np.zeros(unique_track, dtype=np.int))

In [16]:
for i in tqdm(lh['uid'].unique()):
    user = lh[lh['uid'] == i]
    max_value = max(user['count'])
    normalized_list[i] = [j *5 / max_value for j in counting_list[i]]

100%|██████████| 228/228 [00:21<00:00, 10.88it/s]


In [17]:
np.savetxt("../data/normalized_list.csv", normalized_list, delimiter=",")

In [18]:
counting_list

[array([1, 1, 1, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0, 0, 0, ..., 0, 0, 0]),
 array([0,

In [19]:
normalized_list

[[0.10638297872340426,
  0.10638297872340426,
  0.10638297872340426,
  0.10638297872340426,
  1.5957446808510638,
  0.31914893617021278,
  0.10638297872340426,
  0.10638297872340426,
  1.0638297872340425,
  0.10638297872340426,
  0.21276595744680851,
  0.31914893617021278,
  0.31914893617021278,
  0.21276595744680851,
  0.10638297872340426,
  0.21276595744680851,
  0.10638297872340426,
  0.21276595744680851,
  0.10638297872340426,
  0.10638297872340426,
  0.10638297872340426,
  0.21276595744680851,
  0.10638297872340426,
  0.10638297872340426,
  0.10638297872340426,
  0.31914893617021278,
  0.21276595744680851,
  0.31914893617021278,
  0.10638297872340426,
  0.10638297872340426,
  0.10638297872340426,
  0.10638297872340426,
  0.21276595744680851,
  0.31914893617021278,
  0.31914893617021278,
  0.21276595744680851,
  0.31914893617021278,
  0.31914893617021278,
  0.31914893617021278,
  0.42553191489361702,
  1.5957446808510638,
  1.3829787234042554,
  1.3829787234042554,
  1.595744680851

In [20]:
normalized_pd = lh.copy()
normalized_pd.rename(columns={'count':'rating'}, inplace=True)
normalized_pd = normalized_pd.astype({'rating': 'float64'})

In [ ]:
for i in tqdm(range(unique_user)):
    temp = lh[lh['uid'] == i]
    for index, row in temp.iterrows():
        normalized_pd['rating'][index] /= max_list[i]
        normalized_pd['rating'][index] *= 5

  0%|          | 0/228 [00:00<?, ?it/s]/home/han/anaconda3/envs/ts/lib/python3.6/site-packages/ipykernel/__main__.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/home/han/anaconda3/envs/ts/lib/python3.6/site-packages/ipykernel/__main__.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [ ]:
normalized_pd.to_pickle('../data/normalized_pd.pkl')